# Analysis of PIK3CA variants

In the following we compare predictions from Rhapsody, PolyPhen-2, EVmutation and other methods on PIK3CA variants presented in:
* [Dogruluk T et al, *Identification of Variant-Specific Functions of PIK3CA by Rapid Phenotyping of Rare Mutations*, Cancer Res. (2016)](https://www.ncbi.nlm.nih.gov/pmc/articles/PMC4681596/)
* [Zhang Y et al, *A Pan-Cancer Proteogenomic Atlas of PI3K/AKT/mTOR Pathway Alterations*, Cancer Cell (2017)](https://www.sciencedirect.com/science/article/pii/S153561081730168X?via%3Dihub)

In [1]:
import sys, os, pickle, csv, glob
import numpy as np

In [2]:
# Insert here local path to Rhapsody folder
sys.path.insert(0, '../../rhapsody/')

## Import data from papers

In [3]:
# precomputed structured array with data from Dogruluk et al.
data_Dogruluk = pickle.load(open('data/Dogruluk_etal-data.pkl', 'rb'))
data_Dogruluk.dtype.names

('Variant',
 'COSMIC frequency',
 'GF-free survival',
 'Insulin-free survival',
 'Ba/F3',
 'Tumorigenesis',
 'Soft agar colonies',
 'Condel',
 'Condel score',
 'PolyPhen',
 'PolyPhen score',
 'SIFT',
 'SIFT score',
 'MutationAssessor',
 'MutationAssessor score',
 'CanDrA+CTS',
 'CanDrA+CTS score',
 'CanDrA+GEN',
 'CanDrA+GEN score',
 'CHASM driver score',
 'VEST functional score',
 'Mutation Taster',
 'Mutation Taster score')

In [4]:
# PIK3CA data from Zhang et al.
with open('data/Zhang_etal-data.csv') as csv_file:
    csv_read = list(csv.reader(csv_file))
# convert to structured array. Select only PIK3CA missense variants
dt = np.dtype([(f, 'U30') for f in csv_read[2]])
data_Zhang = np.array([x for x in csv_read if x[0]=='PIK3CA' and x[4]=='Missense_Mutation'], dtype=dt)
data_Zhang.dtype.names

('Hugo_Symbol',
 'AA change',
 'Chromosome',
 'Start_position',
 'Variant_Classification',
 'Variant_Type',
 'number of samples',
 'number of patients',
 'Summary pred. functional (no functional assays)',
 'Taylor hotspot',
 'oncogene',
 'Mutation Assessor',
 'Additional literature assessment (D. Kwiatkowski)',
 'BaF3_Call',
 'MCF10A_Call',
 'AKT_pS473',
 'AKT_pT308',
 'MTOR_pS2448',
 'P70S6K_pT389',
 'S6_pS235S236',
 'S6_pS240S244',
 'PI3K/AKT sig',
 'mTOR sig',
 'f23',
 'f24')

## Re-training of unbiased classifier

A few PIK3CA mutations are found in the Integrated Dataset used for training. In order to get completely unbiased predictions, we will retrain a classifier by excluding those variants from the training dataset.

**NB:** The Uniprot names for gene PIK3CA are `P42336` or `PK3CA_HUMAN`.

In [5]:
from rhapsody import *

In [6]:
ID = pickle.load(open('../RF_training/Integrated_Dataset.pkl', 'rb'))

known_PIK3CA_SAVs = [SAV['SAV_coords'] for SAV in ID if SAV['SAV_coords'].startswith('P42336') 
                     or SAV['SAV_coords'].startswith('PK3CA_HUMAN')]
known_PIK3CA_SAVs

['P42336 391 I M',
 'P42336 542 E K',
 'P42336 545 E K',
 'P42336 545 E G',
 'P42336 1047 H R',
 'P42336 1065 H Y',
 'P42336 546 Q P',
 'P42336 343 Y C',
 'P42336 1021 Y H',
 'P42336 1050 G D',
 'P42336 1052 T K',
 'P42336 1065 H L',
 'P42336 1021 Y N',
 'P42336 1025 T N',
 'P42336 453 E Q',
 'P42336 1023 R Q',
 'P42336 542 E V',
 'P42336 546 Q R',
 'P42336 365 E K',
 'P42336 378 C Y',
 'P42336 726 E K',
 'P42336 1025 T A',
 'P42336 1035 A V',
 'P42336 135 E K',
 'P42336 218 E K',
 'P42336 356 V I',
 'P42336 43 I V',
 'P42336 38 R H',
 'P42336 106 G V',
 'P42336 81 E K',
 'P42336 88 R Q',
 'P42336 420 C R',
 'P42336 545 E A',
 'P42336 1021 Y C',
 'P42336 1043 M I',
 'P42336 1047 H Y',
 'P42336 364 G R',
 'P42336 914 G R',
 'P42336 1049 G S',
 'P42336 118 G D',
 'P42336 382 R K',
 'P42336 112 I N',
 'P42336 332 S R']

Let's exclude these variants from the dataset. We will also only consider variants with associated PDB structures larger than 150 residues, which we found to improve prediction accuracy. 

In [7]:
ID_subset = ID[ [i for i,SAV in enumerate(ID) if not SAV['SAV_coords'].startswith('P42336') 
                                                 and SAV['PDB_length']>=150] ]
len(ID_subset)

23346

In [8]:
# complete set of Rhapsody features
full_clsf_featset = ['SAV_coords', 'true_label', 
                     'wt_PSIC', 'Delta_PSIC', 'SASA', 'ANM_MSF-chain', 
                     'ANM_effectiveness-chain', 'ANM_sensitivity-chain',
                     'stiffness-chain', 'entropy', 'ranked_MI', 'BLOSUM']
# reduced set of Rhapsody features (without features computed on Pfam domains)
redx_clsf_featset = [f for f in full_clsf_featset if f not in ['entropy', 'ranked_MI']]

In [ ]:
os.mkdir('results/')

In [ ]:
# training of full classifier
os.mkdir('results/full_clsf')
full_clsf = trainRFclassifier(ID_subset[full_clsf_featset])
for file in glob.glob('*png') + ['trained_classifier.pkl',]:
    os.rename(file, os.path.join('results/full_clsf', file))

In [ ]:
# training of reduced classifier
os.mkdir('results/redx_clsf')
redx_clsf = trainRFclassifier(ID_subset[redx_clsf_featset])
for file in glob.glob('*png') + ['trained_classifier.pkl',]:
    os.rename(file, os.path.join('results/redx_clsf', file))

## Predictions
We will perform a complete scanning of all amino acid variants (*in silico* saturation mutagenesis).

**NB:** PolyPhen-2 predictions are precomputed and saved in `data/pph2`

In [9]:
os.mkdir('results/predictions')
# run rhapsody
rh = rhapsody('data/pph2/pph2-full.txt', 'results/full_clsf/trained_classifier.pkl',
              aux_classifier='results/redx_clsf/trained_classifier.pkl', input_type='PP2')
# store files
for f in glob.glob('rhapsody-*.*'):
    os.rename(f, os.path.join('results/predictions', f))

@> Logging into file: rhapsody-log.txt
@> Logging started at 2019-02-07 18:06:49.133504
@> Imported feature set: 'wt_PSIC'
@>                       'Delta_PSIC'
@>                       'SASA'
@>                       'ANM_MSF-chain'
@>                       'ANM_effectiveness-chain'
@>                       'ANM_sensitivity-chain'
@>                       'stiffness-chain'
@>                       'entropy'
@>                       'ranked_MI'
@>                       'BLOSUM'
@> PolyPhen-2's output parsed.
@> Sequence-conservation features have been retrieved from PolyPhen-2's output.
@> Mapping SAVs to PDB structures...
@> [1/20292] Mapping SAV 'P42336 1 M A' to PDB...
@> Pickle 'UniprotMap-P42336.pkl' recovered.
@> [2/20292] Mapping SAV 'P42336 713 I F' to PDB...
@> [3/20292] Mapping SAV 'P42336 713 I E' to PDB...
@> [4/20292] Mapping SAV 'P42336 713 I D' to PDB...
@> [5/20292] Mapping SAV 'P42336 713 I C' to PDB...
@> [6/20292] Mapping SAV 'P42336 713 I A' to PDB...
@> [7/20292] M

@> [143/20292] Mapping SAV 'P42336 716 T F' to PDB...
@> [144/20292] Mapping SAV 'P42336 716 T E' to PDB...
@> [145/20292] Mapping SAV 'P42336 716 T D' to PDB...
@> [146/20292] Mapping SAV 'P42336 716 T C' to PDB...
@> [147/20292] Mapping SAV 'P42336 715 L M' to PDB...
@> [148/20292] Mapping SAV 'P42336 716 T A' to PDB...
@> [149/20292] Mapping SAV 'P42336 715 L W' to PDB...
@> [150/20292] Mapping SAV 'P42336 715 L V' to PDB...
@> [151/20292] Mapping SAV 'P42336 715 L T' to PDB...
@> [152/20292] Mapping SAV 'P42336 715 L S' to PDB...
@> [153/20292] Mapping SAV 'P42336 715 L R' to PDB...
@> [154/20292] Mapping SAV 'P42336 715 L Q' to PDB...
@> [155/20292] Mapping SAV 'P42336 715 L P' to PDB...
@> [156/20292] Mapping SAV 'P42336 715 L Y' to PDB...
@> [157/20292] Mapping SAV 'P42336 710 E H' to PDB...
@> [158/20292] Mapping SAV 'P42336 710 E G' to PDB...
@> [159/20292] Mapping SAV 'P42336 710 E F' to PDB...
@> [160/20292] Mapping SAV 'P42336 704 R V' to PDB...
@> [161/20292] Mapping SAV '

@> [295/20292] Mapping SAV 'P42336 706 V M' to PDB...
@> [296/20292] Mapping SAV 'P42336 708 A E' to PDB...
@> [297/20292] Mapping SAV 'P42336 707 E C' to PDB...
@> [298/20292] Mapping SAV 'P42336 707 E F' to PDB...
@> [299/20292] Mapping SAV 'P42336 708 A C' to PDB...
@> [300/20292] Mapping SAV 'P42336 707 E Y' to PDB...
@> [301/20292] Mapping SAV 'P42336 707 E W' to PDB...
@> [302/20292] Mapping SAV 'P42336 707 E V' to PDB...
@> [303/20292] Mapping SAV 'P42336 707 E T' to PDB...
@> [304/20292] Mapping SAV 'P42336 707 E S' to PDB...
@> [305/20292] Mapping SAV 'P42336 707 E R' to PDB...
@> [306/20292] Mapping SAV 'P42336 707 E D' to PDB...
@> [307/20292] Mapping SAV 'P42336 707 E Q' to PDB...
@> [308/20292] Mapping SAV 'P42336 707 E N' to PDB...
@> [309/20292] Mapping SAV 'P42336 707 E M' to PDB...
@> [310/20292] Mapping SAV 'P42336 707 E L' to PDB...
@> [311/20292] Mapping SAV 'P42336 707 E K' to PDB...
@> [312/20292] Mapping SAV 'P42336 707 E I' to PDB...
@> [313/20292] Mapping SAV '

@> [447/20292] Mapping SAV 'P42336 731 Q L' to PDB...
@> [448/20292] Mapping SAV 'P42336 731 Q K' to PDB...
@> [449/20292] Mapping SAV 'P42336 731 Q I' to PDB...
@> [450/20292] Mapping SAV 'P42336 731 Q H' to PDB...
@> [451/20292] Mapping SAV 'P42336 731 Q G' to PDB...
@> [452/20292] Mapping SAV 'P42336 731 Q F' to PDB...
@> [453/20292] Mapping SAV 'P42336 731 Q N' to PDB...
@> [454/20292] Mapping SAV 'P42336 731 Q D' to PDB...
@> [455/20292] Mapping SAV 'P42336 732 M D' to PDB...
@> [456/20292] Mapping SAV 'P42336 732 M F' to PDB...
@> [457/20292] Mapping SAV 'P42336 733 K C' to PDB...
@> [458/20292] Mapping SAV 'P42336 733 K A' to PDB...
@> [459/20292] Mapping SAV 'P42336 732 M Y' to PDB...
@> [460/20292] Mapping SAV 'P42336 732 M W' to PDB...
@> [461/20292] Mapping SAV 'P42336 732 M V' to PDB...
@> [462/20292] Mapping SAV 'P42336 732 M T' to PDB...
@> [463/20292] Mapping SAV 'P42336 732 M S' to PDB...
@> [464/20292] Mapping SAV 'P42336 732 M E' to PDB...
@> [465/20292] Mapping SAV '

@> [599/20292] Mapping SAV 'P42336 723 K M' to PDB...
@> [600/20292] Mapping SAV 'P42336 723 K L' to PDB...
@> [601/20292] Mapping SAV 'P42336 723 K I' to PDB...
@> [602/20292] Mapping SAV 'P42336 723 K H' to PDB...
@> [603/20292] Mapping SAV 'P42336 723 K R' to PDB...
@> [604/20292] Mapping SAV 'P42336 723 K G' to PDB...
@> [605/20292] Mapping SAV 'P42336 723 K E' to PDB...
@> [606/20292] Mapping SAV 'P42336 723 K D' to PDB...
@> [607/20292] Mapping SAV 'P42336 723 K C' to PDB...
@> [608/20292] Mapping SAV 'P42336 723 K A' to PDB...
@> [609/20292] Mapping SAV 'P42336 722 E Y' to PDB...
@> [610/20292] Mapping SAV 'P42336 722 E W' to PDB...
@> [611/20292] Mapping SAV 'P42336 722 E V' to PDB...
@> [612/20292] Mapping SAV 'P42336 723 K F' to PDB...
@> [613/20292] Mapping SAV 'P42336 724 K T' to PDB...
@> [614/20292] Mapping SAV 'P42336 723 K S' to PDB...
@> [615/20292] Mapping SAV 'P42336 723 K V' to PDB...
@> [616/20292] Mapping SAV 'P42336 724 K R' to PDB...
@> [617/20292] Mapping SAV '

...

@> [19846/20292] Mapping SAV 'P42336 338 I F' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 338.
@> [19847/20292] Mapping SAV 'P42336 338 I E' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 338.
@> [19848/20292] Mapping SAV 'P42336 338 I D' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 338.
@> [19849/20292] Mapping SAV 'P42336 338 I C' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 338.
@> [19850/20292] Mapping SAV 'P42336 338 I A' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 338.
@> [19851/20292] Mapping SAV 'P42336 337 K Y' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 337.
@> [19852/20292] Mapping SAV 'P42336 337 K W' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 337.
@> [19853/20292] Mapping SAV 'P42336 338 I G' to Pfam...
@> WARNING Unable to compu

@> [19909/20292] Mapping SAV 'P42336 341 A G' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 341.
@> [19910/20292] Mapping SAV 'P42336 341 A F' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 341.
@> [19911/20292] Mapping SAV 'P42336 341 A E' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 341.
@> [19912/20292] Mapping SAV 'P42336 341 A D' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 341.
@> [19913/20292] Mapping SAV 'P42336 341 A L' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 341.
@> [19914/20292] Mapping SAV 'P42336 341 A C' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 341.
@> [19915/20292] Mapping SAV 'P42336 341 A Y' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 341.
@> [19916/20292] Mapping SAV 'P42336 342 T C' to Pfam...
@> WARNING Unable to compu

@> WARNING Unable to compute Pfam features: No Pfam domain for resid 340.
@> [19973/20292] Mapping SAV 'P42336 340 C K' to Pfam...
@> WARNING Unable to compute Pfam features: No Pfam domain for resid 340.
@> [19974/20292] Mapping SAV 'P42336 351 I H' to Pfam...
@> [19975/20292] Mapping SAV 'P42336 351 I K' to Pfam...
@> [19976/20292] Mapping SAV 'P42336 351 I L' to Pfam...
@> [19977/20292] Mapping SAV 'P42336 362 H R' to Pfam...
@> [19978/20292] Mapping SAV 'P42336 362 H Q' to Pfam...
@> [19979/20292] Mapping SAV 'P42336 362 H P' to Pfam...
@> [19980/20292] Mapping SAV 'P42336 362 H N' to Pfam...
@> [19981/20292] Mapping SAV 'P42336 362 H M' to Pfam...
@> [19982/20292] Mapping SAV 'P42336 362 H L' to Pfam...
@> [19983/20292] Mapping SAV 'P42336 362 H K' to Pfam...
@> [19984/20292] Mapping SAV 'P42336 362 H I' to Pfam...
@> [19985/20292] Mapping SAV 'P42336 362 H G' to Pfam...
@> [19986/20292] Mapping SAV 'P42336 362 H F' to Pfam...
@> [19987/20292] Mapping SAV 'P42336 362 H E' to Pfam.

@> [20115/20292] Mapping SAV 'P42336 365 E A' to Pfam...
@> [20116/20292] Mapping SAV 'P42336 365 E V' to Pfam...
@> [20117/20292] Mapping SAV 'P42336 365 E T' to Pfam...
@> [20118/20292] Mapping SAV 'P42336 365 E S' to Pfam...
@> [20119/20292] Mapping SAV 'P42336 365 E R' to Pfam...
@> [20120/20292] Mapping SAV 'P42336 365 E Q' to Pfam...
@> [20121/20292] Mapping SAV 'P42336 365 E P' to Pfam...
@> [20122/20292] Mapping SAV 'P42336 365 E N' to Pfam...
@> [20123/20292] Mapping SAV 'P42336 364 G Y' to Pfam...
@> [20124/20292] Mapping SAV 'P42336 365 E M' to Pfam...
@> [20125/20292] Mapping SAV 'P42336 365 E K' to Pfam...
@> [20126/20292] Mapping SAV 'P42336 365 E I' to Pfam...
@> [20127/20292] Mapping SAV 'P42336 365 E H' to Pfam...
@> [20128/20292] Mapping SAV 'P42336 365 E G' to Pfam...
@> [20129/20292] Mapping SAV 'P42336 365 E F' to Pfam...
@> [20130/20292] Mapping SAV 'P42336 365 E D' to Pfam...
@> [20131/20292] Mapping SAV 'P42336 365 E C' to Pfam...
@> [20132/20292] Mapping SAV 'P

@> [20259/20292] Mapping SAV 'P42336 356 V F' to Pfam...
@> [20260/20292] Mapping SAV 'P42336 356 V E' to Pfam...
@> [20261/20292] Mapping SAV 'P42336 356 V D' to Pfam...
@> [20262/20292] Mapping SAV 'P42336 356 V L' to Pfam...
@> [20263/20292] Mapping SAV 'P42336 356 V C' to Pfam...
@> [20264/20292] Mapping SAV 'P42336 355 Y W' to Pfam...
@> [20265/20292] Mapping SAV 'P42336 355 Y V' to Pfam...
@> [20266/20292] Mapping SAV 'P42336 355 Y T' to Pfam...
@> [20267/20292] Mapping SAV 'P42336 355 Y S' to Pfam...
@> [20268/20292] Mapping SAV 'P42336 355 Y R' to Pfam...
@> [20269/20292] Mapping SAV 'P42336 355 Y Q' to Pfam...
@> [20270/20292] Mapping SAV 'P42336 355 Y P' to Pfam...
@> [20271/20292] Mapping SAV 'P42336 356 V A' to Pfam...
@> [20272/20292] Mapping SAV 'P42336 357 R N' to Pfam...
@> [20273/20292] Mapping SAV 'P42336 356 V M' to Pfam...
@> [20274/20292] Mapping SAV 'P42336 356 V P' to Pfam...
@> [20275/20292] Mapping SAV 'P42336 357 R L' to Pfam...
@> [20276/20292] Mapping SAV 'P

In [10]:
# import EVmutation scores
rh.calcEVmutationFeats()

@> Recovering EVmutation data...
@> EVmutation scores recovered in 31.3s.


array([(nan, nan, nan, nan), (nan, nan, nan, nan), (nan, nan, nan, nan),
       ..., (nan, nan, nan, nan), (nan, nan, nan, nan),
       (nan, nan, nan, nan)],
      dtype=[('EVmut-DeltaE_epist', '<f4'), ('EVmut-DeltaE_indep', '<f4'), ('EVmut-mut_aa_freq', '<f4'), ('EVmut-wt_aa_cons', '<f4')])

## Comparison with experimental data from Dogruluk et al.

In [11]:
assays = ['GF-free survival', 'Insulin-free survival', 'Ba/F3', 'Tumorigenesis', 'Soft agar colonies', 'average']

methods = ['Condel score', 'PolyPhen score', 'SIFT score', 
           'MutationAssessor score', 'CanDrA+CTS score', 'CanDrA+GEN score', 
           'CHASM driver score', 'VEST functional score', 'Mutation Taster score',
           'rhapsody', 'EVmutation', 'PP2']

In [15]:
# select given variants among Rhapsody results
sel = []
for var in data_Dogruluk['Variant']:
    SAV = f'P42336 {var[1:-1]} {var[0]} {var[-1]}'
    sel.append( np.where(rh.SAVcoords['text'] == SAV)[0][0] )

rhaps_preds = rh.mixPreds['path. probability'][sel]
EVmut_preds = - rh.calcEVmutationFeats()['EVmut-DeltaE_epist'][sel]
pph2_preds  = np.array([l['pph2_prob'] for l in rh.PP2output], dtype=float)[sel]

In [40]:
from sklearn.metrics import roc_auc_score as auroc

print(' '*18 + '  '.join([f'{m[:13]:<14}' for m in assays]))

for method in methods:
    if method == 'rhapsody':
        preds = rhaps_preds
    elif method == 'EVmutation':
        preds = EVmut_preds
    elif method == 'PP2':
        preds = pph2_preds
    else:
        preds = data_Dogruluk[method]
    corrs = []
    aurocs = []
    for assay in assays:
        if assay == 'average':
            all_assays = data_Dogruluk[assays[:-1]]
            exp_data = [np.nanmean(list(r)) for r in all_assays]
        else:
            exp_data = data_Dogruluk[assay]
        # skip invalid (NaN) values
        exp_data = np.array( exp_data )
        preds    = np.array( preds )
        sel = np.isnan(exp_data * preds)
        # compute AUROC
        bin_labels = np.where(exp_data[~sel]<2, 0, 1)
        aurocs.append(auroc(bin_labels, preds[~sel]))
        
    m = method.replace(' score', '')
    print(f'{m:<17} ' + '  '.join([f'{a:<13.3f} ' for a in aurocs]))

                  GF-free survi   Insulin-free    Ba/F3           Tumorigenesis   Soft agar col   average       
Condel            0.604           0.483           0.604           0.389           0.497           0.530         
PolyPhen          0.696           0.493           0.696           0.500           0.556           0.652         
SIFT              0.509           0.500           0.509           0.692           0.583           0.573         
MutationAssessor  0.616           0.441           0.616           0.442           0.580           0.573         
CanDrA+CTS        0.554           0.403           0.554           0.500           0.562           0.570         
CanDrA+GEN        0.682           0.627           0.682           0.688           0.794           0.715         
CHASM driver      0.387           0.434           0.387           0.428           0.497           0.394         
VEST functional   0.685           0.646           0.685           0.567           0.556         

### Active *vs* inactive state
Rhapsody automatically maps variants onto PDB `4Q21`, which is the GDP-complexed **inactive** structure. What happens when using the **active** (GTP-bound) structure `6Q21`?

In [ ]:
r_full   = pickle.load(open('results/rhapsody-pickle.pkl', 'rb'))
r_EVmut  = pickle.load(open('results-EVmut/rhapsody-pickle.pkl', 'rb'))
r_active = pickle.load(open('results-active_state/rhapsody-pickle.pkl', 'rb'))

### Recover  PolyPhen-2  and  EVmutation scores
**NB:** I define `EVmut_score` as $- \Delta$E.

In [ ]:
PP2_probs = np.array([float(l['pph2_prob']) for l in r_full.PP2output])
PP2_DeltaPSIC = r_full.featMatrix[:,1]
EVmut_score = - r_EVmut.featMatrix[:,-1]

# Figures
### Inactive/active 

In [ ]:
from scipy.stats.stats import spearmanr
import matplotlib.pyplot as plt
plt.rcParams.update({'font.size': 14, 'font.family': 'Arial'})

score_inactive = r_full.mixedPreds['score']
score_active =   r_active.mixedPreds['score']

fig, ax = plt.subplots(figsize=(6,6))
ax.scatter(score_inactive, score_active, marker='.')
ax.set_xlabel('score for inactive state (PDBID: 4Q21)')
ax.set_ylabel('score for active state (PDBID: 6Q21)')

sel = np.logical_and(~np.isnan(score_inactive), ~np.isnan(score_active))
rho = spearmanr(score_inactive[sel], score_active[sel])[0]

s = r'$\rho$'
ax.set_title('RHAPSODY predictions on active/inactive state')
ax.text(0.8, 0.1, f'{s} = {rho:5.3f}')

fig.tight_layout()
plt.savefig(f'figures/active_vs_inactive_correlation.png', dpi=300)

### Correlation with experiments

In [ ]:
tables = {}

for case, d in data.items():
    resids = d[0][1:]
    wt_aas = d[1][1:]
    table = {}
    for line in d[2:]:
        mut_aa = line[0]
        for i, x in enumerate(line[1:]):
            resid = int(resids[i])
            wt_aa = wt_aas[i]
            table[f'P01112 {resid} {wt_aa} {mut_aa}'] = float(x)
    tables[case] = table

In [ ]:
SAV_coords = r_full.SAVcoords['text']

exp_scores = {}
for case, table in tables.items():
    a = np.zeros(len(SAV_coords))
    a[:] = np.nan
    for i, SAV in enumerate(SAV_coords):
        if SAV in table:
            a[i] = table[SAV]
    exp_scores[case] = a

In [ ]:
exp_scores

In [ ]:
from scipy.stats.stats import spearmanr
import matplotlib.pyplot as plt
plt.rcParams.update({'font.size': 13, 'font.family': 'Arial'})

rhaps_score = r_full.mixedPreds['score']
rhaps_score_act = r_active.mixedPreds['score']
avg_rhaps_score = np.mean(rhaps_score.reshape((-1, 19)), axis=1)
avg_rhaps_score_act = np.mean(rhaps_score_act.reshape((-1, 19)), axis=1)
avg_EVmut_score = np.mean(EVmut_score.reshape((-1, 19)), axis=1)
avg_PP2_probs   = np.mean(PP2_probs.reshape((-1, 19)),   axis=1)

for case, exp_score in exp_scores.items():
    
    avg_exp_score = np.mean(exp_score.reshape((-1, 19)), axis=1)
    
    fig, (ax1, ax2, ax3, ax4) = plt.subplots(1, 4, figsize=(15,4))
    ax1.scatter(exp_score, rhaps_score, marker='.')
    ax2.scatter(exp_score, rhaps_score_act, marker='.')
    ax3.scatter(exp_score, EVmut_score, marker='.')
    ax4.scatter(exp_score, PP2_probs, marker='.')
    ax1.scatter(avg_exp_score, avg_rhaps_score, marker='.', c='r')
    ax2.scatter(avg_exp_score, avg_rhaps_score_act, marker='.', c='r')
    ax3.scatter(avg_exp_score, avg_EVmut_score, marker='.', c='r')
    ax4.scatter(avg_exp_score, avg_PP2_probs,   marker='.', c='r')    
    ax1.set_ylabel('RHAPSODY (inactive state)')
    ax2.set_ylabel('RHAPSODY (active state)')
    ax3.set_ylabel('EVmutation')
    ax4.set_ylabel('PolyPhen-2')

    rho = []
    for i,s in enumerate([rhaps_score, rhaps_score_act, EVmut_score, PP2_probs]):
        sel = np.logical_and(~np.isnan(exp_score), ~np.isnan(s))
        rho.append( spearmanr(exp_score[sel], s[sel])[0] )
    rho_av = []
    for i,s in enumerate([avg_rhaps_score, avg_rhaps_score_act, avg_EVmut_score, avg_PP2_probs]):
        sel = np.logical_and(~np.isnan(avg_exp_score), ~np.isnan(s))
        rho_av.append( spearmanr(avg_exp_score[sel], s[sel])[0] )
    
    s1 = r'$\rho$'
    s2 = r'$\rho_{av}$'
    c  = case.split('_')[0]
    ax1.set_title(f'{c}: {s1}={rho[0]:5.2f}, {s2}={rho_av[0]:5.2f}')
    ax2.set_title(f'{c}: {s1}={rho[1]:5.2f}, {s2}={rho_av[1]:5.2f}')
    ax3.set_title(f'{c}: {s1}={rho[2]:5.2f}, {s2}={rho_av[2]:5.2f}')
    ax4.set_title(f'{c}: {s1}={rho[3]:5.2f}, {s2}={rho_av[3]:5.2f}')
    for ax in (ax1, ax2, ax3, ax4):
        ax.set_xlim((-1.2, 0.7))
        ax.set_xlabel('exp. ΔE')
    fig.tight_layout()
    plt.savefig(f'figures/correlation-{case}.png', dpi=300)

### Mutagenesis table - inactive state
We would like to generate a 20xN matrix (where N is the number of residues) of pathogenicity scores, and take averages of each column, and compare with data on the effect of certain positions in function, multimerization etc.

In [ ]:
JoptEV = 4.551

In [ ]:
probs_full   = r_full.predictions['path. probability']
probs_noPfam = r_full.auxPreds['path. probability']
probs_mixed  = r_full.mixedPreds['path. probability']

In [ ]:
# create empty (20 x num_res) table
num_res = r_full.SAVcoords['pos'][-1]
mut_table = np.zeros((20, num_res), dtype=float)
mut_table[:] = 'nan'
mut_table.shape

In [ ]:
# fill table with predicted probability:
#      1: deleterious
#      0: neutral
# 'nan' : no prediction/wt
aa_list = 'ACDEFGHIKLMNPQRSTVWY'
aa_map  = {aa: i for i, aa in enumerate(aa_list)}
for i, SAV in enumerate(r_full.SAVcoords):
    mut_table[aa_map[SAV['aa_mut']], SAV['pos']-1] = probs_mixed[i]

In [ ]:
# profile of average pathogenicity
_m = probs_mixed.reshape((-1, 19)).T
avg_profile = np.nanmean(_m, axis=0)
min_profile = np.nanmin( _m, axis=0)
max_profile = np.nanmax( _m, axis=0)
# average profile where all features are available
_m = probs_full.reshape((-1, 19)).T
avg_profile_full = np.nanmean(_m, axis=0)

In [ ]:
# normalize EVmutation score (i.e. -ΔE) so that wt=0 and max=100 
# then compute the average over 19 variants
_m = EVmut_score.reshape((-1, 19)).T
avg_EVmut_score = np.nanmean(_m, axis=0)/np.nanmax(EVmut_score)
print('range: {:5.3f} {:5.3f}'.format(np.nanmin(avg_EVmut_score), np.nanmax(avg_EVmut_score)))

In [ ]:
# BETTER: Normalize EVmutation score so that the optimal cutoff is mapped to 0.5
_m = EVmut_score.reshape((-1, 19)).T
avg_EVmut_score = np.nanmean(_m, axis=0)/JoptEV*.5
print('range: {:5.3f} {:5.3f}'.format(np.nanmin(avg_EVmut_score), np.nanmax(avg_EVmut_score)))

In [ ]:
# compute Spearman corr. coeff. between rhapsody and EVmutation
sel = np.logical_and(~np.isnan(avg_EVmut_score), ~np.isnan(avg_profile))
rho = spearmanr(avg_EVmut_score[sel], avg_profile[sel])[0]

In [ ]:
PDB_lengths = [int(t[2][4]) if isinstance(t[2], tuple) else np.nan for t in r_full.Uniprot2PDBmap]

In [ ]:
upper_strip = np.zeros((2, mut_table.shape[1]))
upper_strip[:] = np.nan
upper_strip[0,:] = np.array(PDB_lengths).reshape((-1, 19))[:,0]

In [ ]:
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec

plt.rcParams.update({'font.size': 22, 'font.family': 'Arial'})

# portions of the sequence to display
min_resid = np.where(~np.isnan(avg_profile))[0][0]  + 1
max_resid = np.where(~np.isnan(avg_profile))[0][-1] + 1
third = int((max_resid - min_resid)/3) + 1
segments = {
#              'whole'      : (min_resid, max_resid),
             'whole'      : (2, 166),
}

for seg, (res_i, res_f) in segments.items():

    fig, ax = plt.subplots(3, 2, figsize=(25,8))
    plt.subplots_adjust(wspace=0.025, hspace=0.15)

    # figure structure
    gs = gridspec.GridSpec(3, 2, width_ratios=[100, 1], height_ratios=[1, 20, 10])
    ax0  = plt.subplot(gs[0, 0]) # secondary structure strip
    ax1  = plt.subplot(gs[1, 0]) # mutagenesis table
    axcb = plt.subplot(gs[1, 1]) # colorbar
    ax2  = plt.subplot(gs[2, 0]) # average profile

    # secondary structure strip
#     ax0.imshow(upper_strip[:, res_i-1:res_f], aspect='auto', cmap='gist_rainbow')
    ax0.imshow(upper_strip[:, res_i-1:res_f], aspect='auto', cmap='cividis_r')
    ax0.set_ylim((-0.45, .45))
    ax0.set_yticks([])
    ax0.set_xticks([])
    
    # mutagenesis table (heatmap)
    matplotlib.cm.coolwarm.set_bad(color='white')
    im = ax1.imshow(mut_table[:, res_i-1:res_f], aspect='auto', cmap='coolwarm')
    axcb.figure.colorbar(im, cax=axcb)
    ax1.set_yticks(np.arange(len(aa_list)))
    ax1.set_yticklabels(aa_list, ha='center', position=(-.01,0), fontsize=14)
    ax1.set_xticks(np.arange(50-res_i%50, res_f-res_i+10, 50))
    ax1.set_xticklabels([])
    ax1.set_ylabel('pathog. probability', labelpad=10)

    # average pathogenicity profile
    x_resids = np.arange(1, len(avg_profile)+1)
    # cutoff line
    ax2.hlines(0.5, -.5, len(avg_profile)+.5, colors='grey', lw=.8, linestyle='dashed')
    # solid line for predictions obtained with full classifier
    ax2.plot(x_resids, avg_profile_full, color='red')
    # dotted line for predictions obtained with reduced classifier, without Pfam features
    _p = np.where(np.isnan(avg_profile_full), avg_profile, avg_profile_full)
    ax2.plot(x_resids, _p, color='red', ls='dotted')
    # shading showing range of values
    ax2.fill_between(x_resids, min_profile, max_profile, alpha=0.5, edgecolor='white', facecolor='salmon')
    # EVmutation profile
    ax2.plot(x_resids, avg_EVmut_score, color='blue', lw=.5)

    ax2.text(res_i, 0.05, r'$\rho=${:4.2f}'.format(rho), fontsize=15)
    ax2.set_xlim((res_i-.5, res_f+.5))
    ax2.set_xlabel('residue number')
    ax2.set_ylim((0, 1))
    ax2.set_ylabel('average', rotation=90, labelpad=10)
    ax2.set_yticklabels([])
    ax2r = ax2.twinx()
    ax2r.set_yticks([0, .5, 1])
    ax2r.set_yticklabels(['0', '0.5', '1'])
    ax2r.tick_params(axis='both', which='major', pad=15)
    
    # fig.tight_layout()
    plt.show()
    fig.savefig('figures/mutagenesis_table-inactive.png', dpi=300)

### Mutagenesis table - active state
We would like to generate a 20xN matrix (where N is the number of residues) of pathogenicity scores, and take averages of each column, and compare with data on the effect of certain positions in function, multimerization etc.

In [ ]:
JoptEV = 4.551

In [ ]:
probs_full   = r_active.predictions['path. probability']
probs_noPfam = r_active.auxPreds['path. probability']
probs_mixed  = r_active.mixedPreds['path. probability']

In [ ]:
# create empty (20 x num_res) table
num_res = r_full.SAVcoords['pos'][-1]
mut_table = np.zeros((20, num_res), dtype=float)
mut_table[:] = 'nan'
mut_table.shape

In [ ]:
# fill table with predicted probability:
#      1: deleterious
#      0: neutral
# 'nan' : no prediction/wt
aa_list = 'ACDEFGHIKLMNPQRSTVWY'
aa_map  = {aa: i for i, aa in enumerate(aa_list)}
for i, SAV in enumerate(r_full.SAVcoords):
    mut_table[aa_map[SAV['aa_mut']], SAV['pos']-1] = probs_mixed[i]

In [ ]:
# profile of average pathogenicity
_m = probs_mixed.reshape((-1, 19)).T
avg_profile = np.nanmean(_m, axis=0)
min_profile = np.nanmin( _m, axis=0)
max_profile = np.nanmax( _m, axis=0)
# average profile where all features are available
_m = probs_full.reshape((-1, 19)).T
avg_profile_full = np.nanmean(_m, axis=0)

In [ ]:
# normalize EVmutation score (i.e. -ΔE) so that wt=0 and max=100 
# then compute the average over 19 variants
_m = EVmut_score.reshape((-1, 19)).T
avg_EVmut_score = np.nanmean(_m, axis=0)/np.nanmax(EVmut_score)
print('range: {:5.3f} {:5.3f}'.format(np.nanmin(avg_EVmut_score), np.nanmax(avg_EVmut_score)))

In [ ]:
# BETTER: Normalize EVmutation score so that the optimal cutoff is mapped to 0.5
_m = EVmut_score.reshape((-1, 19)).T
avg_EVmut_score = np.nanmean(_m, axis=0)/JoptEV*.5
print('range: {:5.3f} {:5.3f}'.format(np.nanmin(avg_EVmut_score), np.nanmax(avg_EVmut_score)))

In [ ]:
# compute Spearman corr. coeff. between rhapsody and EVmutation
sel = np.logical_and(~np.isnan(avg_EVmut_score), ~np.isnan(avg_profile))
rho = spearmanr(avg_EVmut_score[sel], avg_profile[sel])[0]

In [ ]:
PDB_lengths = [int(t[2][4]) if isinstance(t[2], tuple) else np.nan for t in r_full.Uniprot2PDBmap]

In [ ]:
upper_strip = np.zeros((2, mut_table.shape[1]))
upper_strip[:] = np.nan
upper_strip[0,:] = np.array(PDB_lengths).reshape((-1, 19))[:,0]

In [ ]:
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec

plt.rcParams.update({'font.size': 22, 'font.family': 'Arial'})

# portions of the sequence to display
min_resid = np.where(~np.isnan(avg_profile))[0][0]  + 1
max_resid = np.where(~np.isnan(avg_profile))[0][-1] + 1
third = int((max_resid - min_resid)/3) + 1
segments = {
#              'whole'      : (min_resid, max_resid),
             'whole'      : (2, 166),
}

for seg, (res_i, res_f) in segments.items():

    fig, ax = plt.subplots(3, 2, figsize=(25,8))
    plt.subplots_adjust(wspace=0.025, hspace=0.15)

    # figure structure
    gs = gridspec.GridSpec(3, 2, width_ratios=[100, 1], height_ratios=[1, 20, 10])
    ax0  = plt.subplot(gs[0, 0]) # secondary structure strip
    ax1  = plt.subplot(gs[1, 0]) # mutagenesis table
    axcb = plt.subplot(gs[1, 1]) # colorbar
    ax2  = plt.subplot(gs[2, 0]) # average profile

    # secondary structure strip
#     ax0.imshow(upper_strip[:, res_i-1:res_f], aspect='auto', cmap='gist_rainbow')
    ax0.imshow(upper_strip[:, res_i-1:res_f], aspect='auto', cmap='cividis_r')
    ax0.set_ylim((-0.45, .45))
    ax0.set_yticks([])
    ax0.set_xticks([])
    
    # mutagenesis table (heatmap)
    matplotlib.cm.coolwarm.set_bad(color='white')
    im = ax1.imshow(mut_table[:, res_i-1:res_f], aspect='auto', cmap='coolwarm')
    axcb.figure.colorbar(im, cax=axcb)
    ax1.set_yticks(np.arange(len(aa_list)))
    ax1.set_yticklabels(aa_list, ha='center', position=(-.01,0), fontsize=14)
    ax1.set_xticks(np.arange(50-res_i%50, res_f-res_i+10, 50))
    ax1.set_xticklabels([])
    ax1.set_ylabel('pathog. probability', labelpad=10)

    # average pathogenicity profile
    x_resids = np.arange(1, len(avg_profile)+1)
    # cutoff line
    ax2.hlines(0.5, -.5, len(avg_profile)+.5, colors='grey', lw=.8, linestyle='dashed')
    # solid line for predictions obtained with full classifier
    ax2.plot(x_resids, avg_profile_full, color='red')
    # dotted line for predictions obtained with reduced classifier, without Pfam features
    _p = np.where(np.isnan(avg_profile_full), avg_profile, avg_profile_full)
    ax2.plot(x_resids, _p, color='red', ls='dotted')
    # shading showing range of values
    ax2.fill_between(x_resids, min_profile, max_profile, alpha=0.5, edgecolor='white', facecolor='salmon')
    # EVmutation profile
    ax2.plot(x_resids, avg_EVmut_score, color='blue', lw=.5)

    ax2.text(res_i, 0.05, r'$\rho=${:4.2f}'.format(rho), fontsize=15)
    ax2.set_xlim((res_i-.5, res_f+.5))
    ax2.set_xlabel('residue number')
    ax2.set_ylim((0, 1))
    ax2.set_ylabel('average', rotation=90, labelpad=10)
    ax2.set_yticklabels([])
    ax2r = ax2.twinx()
    ax2r.set_yticks([0, .5, 1])
    ax2r.set_yticklabels(['0', '0.5', '1'])
    ax2r.tick_params(axis='both', which='major', pad=15)
    
    # fig.tight_layout()
    plt.show()
    fig.savefig('figures/mutagenesis_table-active.png', dpi=300)

### average profiles on PDB structures

In [ ]:
import numpy as np
from prody import *

_p = r_active.mixedPreds['path. probability']
_m = _p.reshape((-1, 19)).T
avg_prof_active = np.nanmean(_m, axis=0)
_p = r_full.mixedPreds['path. probability']
_m = _p.reshape((-1, 19)).T
avg_prof_inactive = np.nanmean(_m, axis=0)
diff = avg_prof_active - avg_prof_inactive
resids = r_active.SAVcoords['pos'].reshape((-1, 19)).T[0]

print(len(avg_prof_active))
print(len(avg_prof_inactive))

In [ ]:
pdb_active   = parsePDB('6q21', chain='A').select('protein and resid 2 to 166')
pdb_inactive = parsePDB('4q21', chain='A').select('protein and resid 2 to 166')
print(pdb_active.ca.numAtoms())
print(pdb_inactive.ca.numAtoms())

In [ ]:
# replace the B-factor column in chain A with the predictions
PDBresnums = pdb_active.getResnums()
new_betas = np.zeros_like(PDBresnums, dtype=float)
new_betas_diff = np.zeros_like(PDBresnums, dtype=float)
for resid, prob, d in zip(resids, avg_prof_active, diff):
    new_betas[PDBresnums==int(resid)] = prob
    new_betas_diff[PDBresnums==int(resid)] = d
# write modified PDB
pdb_active.setBetas(new_betas)
f = writePDB('figures/mapped_active', pdb_active)
pdb_active.setBetas(new_betas_diff)
f = writePDB('figures/mapped_active_diff', pdb_active)

In [ ]:
# replace the B-factor column in chain A with the predictions
PDBresnums = pdb_inactive.getResnums()
new_betas = np.zeros_like(PDBresnums, dtype=float)
new_betas_diff = np.zeros_like(PDBresnums, dtype=float)
for resid, prob, d in zip(resids, avg_prof_inactive, diff):
    new_betas[PDBresnums==int(resid)] = prob
    try:
        new_betas_diff[PDBresnums==int(resid)] = d
    except:
        pass
# write modified PDB
pdb_inactive.setBetas(new_betas)
f = writePDB('figures/mapped_inactive', pdb_inactive)
pdb_inactive.setBetas(new_betas_diff)
f = writePDB('figures/mapped_inactive_diff', pdb_inactive)

In [ ]:
plt.hist(diff[~np.isnan(diff)])

In [ ]:
sel = ~np.isnan(diff)
_diff   = diff[sel]
_resids = resids[sel]
_resids[np.argsort(-_diff)][:5]

# Predictions on known variants

In [ ]:
sel = r_full.predictions['training info'] != 'new'
print(r_full.predictions[sel])

In [ ]:
np.nanstd(diff)

In [ ]:
diff[np.isnan(diff)]

### Training of unbiased classifiers